In [29]:
import prestodb
conn=prestodb.dbapi.connect(
    host='localhost',
    port=9000,
    user='python',
    catalog='hive',
    schema='default',
)
cur = conn.cursor()

In [2]:
import json
cur.execute(f"select messagebody from smart_columbus_cve__captcha where os_partition = '2021_01' and messagetype = 'BSM' limit 1")
rows = cur.fetchall()

json.dumps(json.loads(rows[0][0]))

source_table = 'smart_columbus_cve__captcha'
source_device = 'morse_sandylane_cvcp'

os_partition = '2021_01'
day = '5'

In [3]:
geo_bsm_query = f"""
with bsm_subset as (
        select * from {source_table} 
        where os_partition = '{os_partition}' 
        and messagetype = 'BSM' 
        and sourcedevice = '{source_device}'
        and day(from_iso8601_timestamp(timestamp)) = {day}
    ), 

    identified_locations as (
        select 
            cast(json_extract_scalar(messagebody, '$.coreData.lat') as double) / 10000000 as lat, 
            cast(json_extract_scalar(messagebody, '$.coreData.long') as double) / 10000000 as long,
            cast(json_extract_scalar(messagebody, '$.coreData.speed') as double) as speed, 
            json_extract_scalar(messagebody, '$.coreData.id') as id, 
            sourcedevice,
            timestamp
            from bsm_subset
    ),
    
    lane_subset as (select * from smart_columbus_cve__cve_lane_geometries 
        where sourcedevice = '{source_device}' 
        and ingressapproach = 'true' 
        and lanetype = 'vehicle'
    )

    SELECT il.lat, il.long, il.sourcedevice, il.speed, il.timestamp, geo.laneid, geo.front_lat, geo.front_lon, il.id FROM lane_subset geo 
      join identified_locations il 
          on geo.sourcedevice = il.sourcedevice 
          and ST_Contains(ST_GeometryFromText(geo.geometry), ST_Point(il.long, il.lat))
"""

bsm_work_table = "cve_geo_bsm_python_scratch"

cur.execute(f'drop table if exists {bsm_work_table}')
cur.fetchall()

cur.execute(f'create table {bsm_work_table} as {geo_bsm_query}')
cur.fetchall()


[[13812]]

In [4]:
# Maximum difference in seconds between a BSM and its matching SPAT
message_time_tolerance = '0.05'

bsm_to_spat_query = f"""
with bsms_unix as (
    select timestamp, to_unixtime(from_iso8601_timestamp(timestamp)) as unixtime, sourcedevice, laneid
    from {bsm_work_table}
),

spats_unix as (
    select timestamp, to_unixtime(from_iso8601_timestamp(timestamp)) as unixtime, sourcedevice
    from cve_one_day where os_partition = '{os_partition}' and messagetype = 'SPAT' and day(from_iso8601_timestamp(timestamp)) = {day}
),

unix_join as (
    select bsms.timestamp as bsm_timestamp, spats.timestamp as spat_timestamp, spats.sourcedevice, bsms.laneid
    from bsms_unix as bsms join spats_unix as spats on bsms.sourcedevice = spats.sourcedevice and abs(bsms.unixtime - spats.unixtime) < {message_time_tolerance} 
),

deduped_unix_join as (
    select min(spat_timestamp) as spat_timestamp, bsm_timestamp, sourcedevice, laneid
    from unix_join group by bsm_timestamp, sourcedevice, laneid
)

select * from deduped_unix_join
"""

geo_match_table = "cve_geo_match_python_scratch"

cur.execute(f'drop table if exists {geo_match_table}')
cur.fetchall()

cur.execute(f'create table {geo_match_table} as {bsm_to_spat_query}')
cur.fetchall()

[[13683]]

In [5]:
map_query = f"""
with latest_map as (SELECT arbitrary(messagebody) as messagebody, sourcedevice FROM {source_table} where os_partition = '{os_partition}' and messagetype = 'MAP' group by sourcedevice),

extracted_values as (
    select 
           json_extract(messageBody, '$.intersections[0].laneWidth') as laneWidth, 
           cast(json_extract_scalar(messageBody, '$.intersections[0].refPoint.lat') as double) / 10000000 as refLat, 
           cast(json_extract_scalar(messageBody, '$.intersections[0].refPoint.long') as double) / 10000000 as refLon,

           transform(
               cast(json_extract(messageBody, '$.intersections[0].laneSet') AS ARRAY<JSON>),
                 x -> element_at(transform(cast(JSON_EXTRACT(x, '$.nodeList[1]') as ARRAY<JSON>),
                   y -> cast(ROW(
                     JSON_EXTRACT_scalar(x, '$.laneID'), 
                     JSON_EXTRACT_scalar(x, '$.ingressApproach'),
                     cast(transform(cast(JSON_EXTRACT(x, '$.connectsTo') as ARRAY<JSON>), connection -> JSON_EXTRACT_SCALAR(connection, '$.signalGroup')) as ARRAY<VARCHAR>),  
                     JSON_EXTRACT_scalar(y, '$.delta[1].x'), 
                     JSON_EXTRACT_scalar(y, '$.delta[1].y'),
                     JSON_EXTRACT_scalar(x, '$.nodeList[1][1].delta[1].x'), 
                     JSON_EXTRACT_scalar(x, '$.nodeList[1][1].delta[1].y')
                     ) 
                  as ROW(laneID VARCHAR, ingressApproach VARCHAR, signals ARRAY<VARCHAR>, x DOUBLE, y DOUBLE, xOffset DOUBLE, yOffset DOUBLE))
                 ), 1)
            ) as deltas,
    * from latest_map
),
    
extracted_coordinates as (
select transform(deltas, x -> cast(ROW(
  x.laneID, 
  x.ingressApproach, 
  x.signals,
  refLat + (x.y / 100) / 111111, 
  refLon + (x.x / 100) / (111111 * COS(refLat * PI() / 180)),
  MOD(90 - ATAN2(x.yOffset * -1, x.xOffset * -1)*180/PI(),360)
  ) as ROW(laneID VARCHAR, ingressApproach VARCHAR, signals ARRAY<VARCHAR>, lat DOUBLE, lon DOUBLE, laneDirection DOUBLE))) as coordinates, 
  * from extracted_values
),

stop_points as (
    SELECT ingressApproach, sourcedevice, laneID, signals, lat, lon, CASE WHEN laneDirection < 0 THEN laneDirection + 360 else laneDirection END as laneDirection 
    FROM extracted_coordinates CROSS JOIN UNNEST(coordinates) AS t ( laneID, ingressApproach, signals, lat, lon, laneDirection) 
    where ingressApproach is not null
)

select * from stop_points
"""

map_work_table = "cve_geo_map_python_scratch"

cur.execute(f'drop table if exists {map_work_table}')
cur.fetchall()

cur.execute(f'create table {map_work_table} as {map_query}')
cur.fetchall()

[[806]]

In [7]:
spat_query = f"""
with spat_subset as (
    SELECT * FROM cve_one_day where messagetype = 'SPAT' and timestamp in (select spat_timestamp from {geo_match_table}) 
),

signal_states as (
    select 
        sourcedevice, 
        timestamp, 
        transform(
            cast(json_extract(messagebody, '$.intersections[0].states') as ARRAY<JSON>), 
            x -> cast(
                    ROW(
                        json_extract(x, '$.signalGroup'), 
                        json_extract(x, '$["state-time-speed"][0].eventState'),
                        json_extract(x, '$["state-time-speed"][0].timing.minEndTime')
                    ) as ROW(signalGroup VARCHAR, state VARCHAR, minEndTime DOUBLE)
                 )
        ) as signalStates 
    from spat_subset
),

extracted_signal_states as (
    select sourceDevice, timestamp, signalGroup, state, minEndTime
    from signal_states CROSS JOIN UNNEST(signalStates) AS t ( signalGroup, state, minEndTime)
),

lane_signal_groups as (
    select laneID, lat, lon, signalGroup, laneDirection, sourcedevice
    from {map_work_table} CROSS JOIN UNNEST(signals) as t (signalGroup)
),

spat_states as (
    select state, timestamp, laneID, laneDirection, minEndTime
    from lane_signal_groups join extracted_signal_states using (signalGroup, sourcedevice)
),

spat_truthy_states as (
    select state = 'stop-And-Remain' as signal_group_red, timestamp, laneID, laneDirection
    from spat_states
),

spat_lane_states as (
    select every(signal_group_red) as lane_red_light, laneID, laneDirection, timestamp
    from spat_truthy_states group by laneID, timestamp, laneDirection
),

aggregated_states as (
    select array_agg(cast(ROW(state, minEndTime) as ROW(state VARCHAR, minEndTime DOUBLE))) as states, timestamp, laneID, laneDirection from spat_states group by timestamp, laneID, laneDirection
)

select * from aggregated_states
"""

print(spat_query)

spat_work_table = "cve_geo_spat_python_scratch"

cur.execute(f'drop table if exists {spat_work_table}')
cur.fetchall()

cur.execute(f'create table {spat_work_table} as {spat_query}')
cur.fetchall()

cur.execute(f'select * from {spat_work_table} limit 1')
cur.fetchall()


with spat_subset as (
    SELECT * FROM cve_one_day where messagetype = 'SPAT' and timestamp in (select spat_timestamp from cve_geo_match_python_scratch) 
),

signal_states as (
    select 
        sourcedevice, 
        timestamp, 
        transform(
            cast(json_extract(messagebody, '$.intersections[0].states') as ARRAY<JSON>), 
            x -> cast(
                    ROW(
                        json_extract(x, '$.signalGroup'), 
                        json_extract(x, '$["state-time-speed"][0].eventState'),
                        json_extract(x, '$["state-time-speed"][0].timing.minEndTime')
                    ) as ROW(signalGroup VARCHAR, state VARCHAR, minEndTime DOUBLE)
                 )
        ) as signalStates 
    from spat_subset
),

extracted_signal_states as (
    select sourceDevice, timestamp, signalGroup, state, minEndTime
    from signal_states CROSS JOIN UNNEST(signalStates) AS t ( signalGroup, state, minEndTime)
),

lane_signal_groups as (
    select 

[[[['protected-Movement-Allowed', 12345.0]],
  '2021-01-05T13:20:07.239Z',
  '18',
  195.16889487121335]]

In [8]:
final_query = f"""
--- Final Result

select 
    bsms.lat, bsms.long, bsms.timestamp as bsm_timestamp, spat_lane_states.timestamp as spat_timestamp, bsms.id,
    states, dd.laneID, sp.signals, bsms.sourcedevice, bsms.front_lat, bsms.front_lon, bsms.speed * 2.23694 / 50 as speed,
    ST_Distance(
        to_spherical_geography(ST_Point(cast(bsms.front_lon as double), cast(bsms.front_lat as double))), 
        to_spherical_geography(ST_Point(bsms.long, bsms.lat))
    ) * 3.281 as distanceToStop
from {bsm_work_table} bsms
  join {geo_match_table} dd on bsms.timestamp = dd.bsm_timestamp and bsms.laneID = dd.laneID
  join {spat_work_table} spat_lane_states on spat_lane_states.timestamp = dd.spat_timestamp and spat_lane_states.laneID = dd.laneID
  join {map_work_table} sp on sp.laneID = dd.laneID
"""

print(final_query)

final_work_table = "cve_geo_final_python_scratch"

cur.execute(f'drop table if exists {final_work_table}')
cur.fetchall()

cur.execute(f'create table {final_work_table} as {final_query}')
cur.fetchall()

cur.execute(f'select * from {final_work_table} limit 1')
cur.fetchall()


--- Final Result

select 
    bsms.lat, bsms.long, bsms.timestamp as bsm_timestamp, spat_lane_states.timestamp as spat_timestamp, bsms.id,
    states, dd.laneID, sp.signals, bsms.sourcedevice, bsms.front_lat, bsms.front_lon, bsms.speed * 2.23694 / 50 as speed,
    ST_Distance(
        to_spherical_geography(ST_Point(cast(bsms.front_lon as double), cast(bsms.front_lat as double))), 
        to_spherical_geography(ST_Point(bsms.long, bsms.lat))
    ) * 3.281 as distanceToStop
from cve_geo_bsm_python_scratch bsms
  join cve_geo_match_python_scratch dd on bsms.timestamp = dd.bsm_timestamp and bsms.laneID = dd.laneID
  join cve_geo_spat_python_scratch spat_lane_states on spat_lane_states.timestamp = dd.spat_timestamp and spat_lane_states.laneID = dd.laneID
  join cve_geo_map_python_scratch sp on sp.laneID = dd.laneID



[[40.0613943,
  -82.9942427,
  '2021-01-05T15:06:07.416Z',
  '2021-01-05T15:06:07.439Z',
  '2025686045',
  [['protected-Movement-Allowed', 4381.0]],
  '115',
  ['6'],
  'morse_sandylane_cvcp',
  '40.06133047995518',
  '-82.99274810080972',
  29.974996,
  417.9792805094341]]

Distance to stop
    Off by a bit (20%?)
    Lat/Lon swapped

ConditionB
    Crit Distance to Distance to Stop Backwards?

Time To Next Phase
    Use Max?
    Second of the hour * 10
    Unit conversion needed
    Time wraps
        if ttnp < -20
            then add 3600
    
Add IDs to final data

In [16]:
# 	if ((SPAT.SignalState = 7 || SPAT.SignalState = 8) && (tToStopbar  > SPAT.timeNextphase))  TBD!
#      ||  (SPAT.SignalState = 3 and (criticalDist1 > dToStopbar){
# 		conditionA = TRUE;
# 	}
# 	if ((tToStopbar < warnTime) && (criticalDist1 > dToStopbar)) ||  criticalDist2 > dToStopbar {
# 		conditionB = TRUE
# 	}
# 	redLightWarningEvent = FALSE;
# 	if conditionA && conditionB{
# 		redLightWarningEvent = TRUE:
# 	}

warning_issue_query = f"""
with parameters as (select *,
    all_match(states, state -> state.state = 'stop-And-Remain') as red_light,
    any_match(states, state -> state.state = 'permissive-clearance' or state.state = 'protected-clearance') as yellow_light,
    states[1].minEndTime as timeNextphase,
    2.5 as prt,
    10 as criticalAccel,
    1 + 1.47 * speed / 20 as warnTime,
    distanceToStop / (speed * 1.47) as timeToSB,
    MINUTE(from_iso8601_timestamp(spat_timestamp)) * 600 
    + second(from_iso8601_timestamp(spat_timestamp)) * 10
    + millisecond(from_iso8601_timestamp(spat_timestamp)) / 100 as spat_time_as_moh
from {final_work_table} where speed > 0),

critical_distance as (select *, 
    1.47 * speed * prt + speed * speed / (2 * criticalAccel) as criticalDist,
    (timeNextphase - spat_time_as_moh) / 10 as timeToNextPhase
from parameters),

looped_time_to_next_phase as (
    select *, 
        case when timeToNextPhase < -20 then timeToNextPhase + 3600 else timeToNextPhase end as adjtimeToNextPhase
    from critical_distance
),

both_conditions as (select *,
    case when ((yellow_light = true) and (timeToSB > adjtimeToNextPhase)) 
                or (red_light = true and criticalDist > distanceToStop) 
                then true else false end as conditionA,
    case when ((timeToSB < warnTime) and (criticalDist < distanceToStop)) 
                or criticalDist > distanceToStop 
                then true else false end as conditionB
from looped_time_to_next_phase)

select case when conditionb = true and conditiona = true then true else false end as warning_issued, * from both_conditions
"""

warnings_table = "cve_warnings_python_scratch"

cur.execute(f'drop table if exists {warnings_table}')
cur.fetchall()

cur.execute(f'create table {warnings_table} as {warning_issue_query}')
cur.fetchall()

cur.execute(f'select count(1), conditionA, conditionB from {warnings_table} group by conditionA, conditionB')
print(cur.fetchall())

cur.execute(f'select * from {warnings_table}')
rows = cur.fetchall()

import pandas as pd

columns = list(map(lambda x: x[0], cur.description))

df = pd.DataFrame(rows, columns = columns)

pd.set_option('display.max_columns', None)
df.to_csv('warning_data.csv', index=False)
df
df.sort_values(by=['adjtimetonextphase'])

[[453612, False, False], [97283, False, True], [13483, True, False], [13334, True, True]]


warning_issued        lat       long             bsm_timestamp  \
261527           False  40.061363 -82.993962  2021-01-05T10:22:50.903Z   
261535           False  40.061363 -82.993962  2021-01-05T10:22:50.903Z   
261534           False  40.061363 -82.993962  2021-01-05T10:22:50.903Z   
261532           False  40.061363 -82.993962  2021-01-05T10:22:50.903Z   
261531           False  40.061363 -82.993962  2021-01-05T10:22:50.903Z   
...                ...        ...        ...                       ...   
417911           False  40.061360 -82.989043  2021-01-05T14:42:49.141Z   
417912           False  40.061360 -82.989043  2021-01-05T14:42:49.141Z   
417913           False  40.061360 -82.989043  2021-01-05T14:42:49.141Z   
417937           False  40.061360 -82.989043  2021-01-05T14:42:49.141Z   
417896           False  40.061360 -82.989043  2021-01-05T14:42:49.141Z   

                  spat_timestamp          id  \
261527  2021-01-05T10:22:50.939Z  1237475418   
261535  2021-01-05T10:22:50.939Z  1237475418   
261534  2021-01-05T10:22:50.939Z  1237475418   
261532  2021-01-05T10:22:50.939Z  1237475418   
261531  2021-01-05T10:22:50.939Z  1237475418   
...                          ...         ...   
417911  2021-01-05T14:42:49.138Z  4237402898   
417912  2021-01-05T14:42:49.138Z  4237402898   
417913  2021-01-05T14:42:49.138Z  4237402898   
417937  2021-01-05T14:42:49.138Z  4237402898   
417896  2021-01-05T14:42:49.138Z  4237402898   

                                                   states laneid    signals  \
261527                   [[protected-clearance, 13574.0]]    114      [111]   
261535                   [[protected-clearance, 13574.0]]    114  [6, 6, 6]   
261534                   [[protected-clearance, 13574.0]]    114     [6, 6]   
261532                   [[protected-clearance, 13574.0]]    114     [8, 8]   
261531                   [[protected-clearance, 13574.0]]    114        [5]   
...                                                   ...    ...        ...   
417911  [[stop-And-Remain, 25476.0], [stop-And-Remain,...     50        [2]   
417912  [[stop-And-Remain, 25476.0], [stop-And-Remain,...     50     [3, 3]   
417913  [[stop-And-Remain, 25476.0], [stop-And-Remain,...     50      [111]   
417937  [[stop-And-Remain, 25476.0], [stop-And-Remain,...     50        [2]   
417896  [[stop-And-Remain, 25476.0], [stop-And-Remain,...     50     [2, 2]   

                sourcedevice          front_lat           front_lon  \
261527  morse_sandylane_cvcp  40.06129717992188  -82.99274974710526   
261535  morse_sandylane_cvcp  40.06129717992188  -82.99274974710526   
261534  morse_sandylane_cvcp  40.06129717992188  -82.99274974710526   
261532  morse_sandylane_cvcp  40.06129717992188  -82.99274974710526   
261531  morse_sandylane_cvcp  40.06129717992188  -82.99274974710526   
...                      ...                ...                 ...   
417911  morse_sandylane_cvcp   40.0614725000972  -82.99224292326488   
417912  morse_sandylane_cvcp   40.0614725000972  -82.99224292326488   
417913  morse_sandylane_cvcp   40.0614725000972  -82.99224292326488   
417937  morse_sandylane_cvcp   40.0614725000972  -82.99224292326488   
417896  morse_sandylane_cvcp   40.0614725000972  -82.99224292326488   

            speed  distancetostop  red_light  yellow_light  timenextphase  \
261527  23.487870      339.279401      False          True        13574.0   
261535  23.487870      339.279401      False          True        13574.0   
261534  23.487870      339.279401      False          True        13574.0   
261532  23.487870      339.279401      False          True        13574.0   
261531  23.487870      339.279401      False          True        13574.0   
...           ...             ...        ...           ...            ...   
417911  30.825033      894.304003       True         False        25476.0   
417912  30.825033      894.304003       True         False        25476.0   
417913  30.825033      894.304003       True   

In [30]:
cur.execute(f"""
with warned_vehicles as (select distinct(id) from {warnings_table} where warning_issued = true)
select * from {warnings_table} where id in (select * from warned_vehicles limit 3)
""")
rows = cur.fetchall()

columns = list(map(lambda x: x[0], cur.description))

warned_vehicles = pd.DataFrame(rows, columns = columns)

warned_vehicles

warning_issued        lat       long             bsm_timestamp  \
0               False  40.061315 -82.993278  2021-01-05T22:22:31.561Z   
1               False  40.061315 -82.993278  2021-01-05T22:22:31.561Z   
2               False  40.061315 -82.993278  2021-01-05T22:22:31.561Z   
3               False  40.061315 -82.993278  2021-01-05T22:22:31.561Z   
4               False  40.061315 -82.993278  2021-01-05T22:22:31.561Z   
...               ...        ...        ...                       ...   
19936            True  40.061416 -82.991554  2021-01-05T00:01:41.426Z   
19937            True  40.061416 -82.991554  2021-01-05T00:01:41.426Z   
19938            True  40.061416 -82.991554  2021-01-05T00:01:41.426Z   
19939            True  40.061416 -82.991554  2021-01-05T00:01:41.426Z   
19940            True  40.061416 -82.991554  2021-01-05T00:01:41.426Z   

                 spat_timestamp          id  \
0      2021-01-05T22:22:31.553Z  1031541917   
1      2021-01-05T22:22:31.553Z  1031541917   
2      2021-01-05T22:22:31.553Z  1031541917   
3      2021-01-05T22:22:31.553Z  1031541917   
4      2021-01-05T22:22:31.553Z  1031541917   
...                         ...         ...   
19936  2021-01-05T00:01:41.439Z  3799884027   
19937  2021-01-05T00:01:41.439Z  3799884027   
19938  2021-01-05T00:01:41.439Z  3799884027   
19939  2021-01-05T00:01:41.439Z  3799884027   
19940  2021-01-05T00:01:41.439Z  3799884027   

                                                  states laneid     signals  \
0      [[stop-And-Remain, 13609.0], [stop-And-Remain,...    114       [255]   
1      [[stop-And-Remain, 13609.0], [stop-And-Remain,...    114         [6]   
2      [[stop-And-Remain, 13609.0], [stop-And-Remain,...    114      [2, 2]   
3      [[stop-And-Remain, 13609.0], [stop-And-Remain,...    114      [6, 6]   
4      [[stop-And-Remain, 13609.0], [stop-And-Remain,...    114         [6]   
...                                                  ...    ...         ...   
19936                        [[stop-And-Remain, 1500.0]]     51         [2]   
19937                        [[stop-And-Remain, 1500.0]]     51         [1]   
19938                        [[stop-And-Remain, 1500.0]]     51  [183, 183]   
19939                        [[stop-And-Remain, 1500.0]]     51       [125]   
19940                        [[stop-And-Remain, 1500.0]]     51       [125]   

               sourcedevice          front_lat           front_lon      speed  \
0      morse_sandylane_cvcp  40.06129717992188  -82.99274974710526  23.711564   
1      morse_sandylane_cvcp  40.06129717992188  -82.99274974710526  23.711564   
2      morse_sandylane_cvcp  40.06129717992188  -82.99274974710526  23.711564   
3      morse_sandylane_cvcp  40.06129717992188  -82.99274974710526  23.711564   
4      morse_sandylane_cvcp  40.06129717992188  -82.99274974710526  23.711564   
...                     ...                ...                 ...        ...   
19936  morse_sandylane_cvcp  40.06144604007074   -82.9922469214112  63.036969   
19937  morse_sandylane_cvcp  40.06144604007074   -82.9922469214112  63.036969   
19938  morse_sandylane_cvcp  40.06144604007074   -82.9922469214112  63.036969   
19939  morse_sandylane_cvcp  40.06144604007074   -82.9922469214112  63.036969   
19940  morse_sandylane_cvcp  40.06144604007074   -82.9922469214112  63.036969   

       distancetostop  red_light  yellow_light  timenextphase  prt  \
0          147.500770       True         False        13609.0  2.5   
1          147.500770       True         False        13609.0  2.5   
2          147.500770       True         False        13609.0  2.5   
3          147.500770       True         False        13609.0  2.5   
4          147.500770       True         False        13609.0  2.5   
...               ...        ...           ...            ...  ...   
19936      193.745961       True         False         1500.0  2.5   
19937      193.745961       True         False         1500.0  2.5   
19938      19

In [31]:
import plotly.express as px
fig = px.scatter_mapbox(warned_vehicles, lat="lat", lon="long",     color="id",
                  color_continuous_scale=px.colors.cyclical.IceFire, zoom=14.5,
                        hover_data=["speed", "timetonextphase", "red_light", "yellow_light"]
                  )
fig.update_layout(mapbox_style="satellite", mapbox_accesstoken="pk.eyJ1Ijoic21ydGNidXMiLCJhIjoiY2ptMTB6YjIzMGVuazNwcWcyczk3a2ZmNSJ9.SjVhquTC7K5RzbGqoGZUYg")
fig.show()